In [1]:
import plotly_express as px  # import plotly.express as px
import plotly.graph_objects as go
import pandas as pd
import numpy as np
import os

name = ["NeRF", "PANO", "OURS+", "OURS"]
foveal = 8.0
mid = 2.8
far = 2.6
blend = 0.1
ours_full = 562
pano = 1e4
nerf = 9e4

times = {
    "fovea_l": 0,
    "mid_l": 0,
    "far_l": 0,
    "fovea_r": 0,
    "mid_r": 0,
    "far_r": 0,
    "blend": 0,
    "ours_full": 0,
    "pano": 0,
    "nerf": 0,
}
clip = 0
frame_id = 0


def calc_total():
    return [
        times["nerf"],
        times["pano"],
        times["ours_full"],
        times["fovea_l"] + times["mid_l"] + times["far_l"] +
            times["fovea_r"] + times["mid_r"] + times["far_r"] + times["blend"]
    ]


def draw_frame(*, xlim=None, **kwargs):
    global frame_id
    for key in kwargs:
        times[key] = kwargs[key]
    tot = calc_total()
    data = {
        "fovea_l": [0, 0, 0, times["fovea_l"]],
        "mid_l": [0, 0, 0, times["mid_l"]],
        "far_l": [0, 0, 0, times["far_l"]],
        "fovea_r": [0, 0, 0, times["fovea_r"]],
        "mid_r": [0, 0, 0, times["mid_r"]],
        "far_r": [0, 0, 0, times["far_r"]],
        "blend": [0, 0, 0, times["blend"]],
        "ours_full": [0, 0, times["ours_full"], 0],
        "pano": [0, times["pano"], 0, 0],
        "nerf": [times["nerf"], 0, 0, 0],
    }
    if xlim is None or xlim < max(tot) * 1.1:
        xlim = max(tot) * 1.1
    
    fig = go.Figure()
    times_keys = list(times.keys())
    for key in times_keys:
        if key == times_keys[-1]:
            fig.add_trace(go.Bar(
                y=name,
                x=data[key],
                name=key,
                orientation='h',
                text=["" if item == 0 else f"{item:.1f}" if item < 1000 else f"{item:.1e}" for item in tot],
                textposition="outside"
            ))
        else:
            fig.add_trace(go.Bar(
                y=name,
                x=data[key],
                name=key,
                orientation='h',
            ))
    fig.update_traces(width=0.5)
    fig.update_layout(barmode='stack', showlegend=False,
                      yaxis_visible=False, yaxis_showticklabels=False, xaxis_range=[0, xlim])
    
    # fig.show()
    fig.write_image(f"dynamic_bar/clip_{clip}/{frame_id:04d}.png", width=1920 // 2, height=1080 // 2, scale=2)
    frame_id = frame_id + 1

def add_animation(*, frames, xlim=None, **kwargs):
    if frames == 1:
        draw_frame(**kwargs, xlim=xlim)
        return
    data = {
        key: np.linspace(times[key], kwargs[key], frames)
        for key in kwargs
    }
    for i in range(frames):
        draw_frame(**{key: data[key][i] for key in data}, xlim=xlim)

def new_clip():
    global clip, frame_id
    clip += 1
    frame_id = 0
    os.system(f"mkdir dynamic_bar/clip_{clip}")

os.system('rm -f -r dynamic_bar')
os.system('mkdir dynamic_bar')

# ours mono
new_clip()
add_animation(fovea_l=foveal, frames=48, xlim=30)   # Step 1: grow foveal
add_animation(mid_l=mid, frames=16, xlim=30)         # Step 2: grow mid
add_animation(far_l=far, frames=16, xlim=30)         # Step 3: grow far
add_animation(blend=blend, frames=1, xlim=30)     # Step 4: grow blend

# ours stereo
new_clip()
add_animation(fovea_r=foveal, frames=24, xlim=30)   # Step 1: grow foveal
add_animation(mid_r=mid, frames=8, xlim=30)         # Step 2: grow mid
add_animation(far_r=far, frames=8, xlim=30)         # Step 3: grow far

# ours stereo adapt
new_clip()
add_animation(mid_r=0, far_r=0, frames=24, xlim=30)

# other series
new_clip()
add_animation(ours_full=ours_full, frames=48, xlim=30)
new_clip()
add_animation(pano=pano, frames=48, xlim=30)
new_clip()
add_animation(nerf=nerf, frames=48, xlim=30)

#os.system(f'ffmpeg -y -r 24 -i dynamic_bar/%04d.png dynamic_bar.avi')

In [ ]:
fig = px.bar(
    df1,  # 绘图数据
    x=list(times.keys()),    # y轴
    y="name",  # x轴
    orientation='h',   # 水平柱状图
    #text=[["a", "tot"], "tot1", "tot2", {"fovea_l": "", "blend_r": 13.5}]   # 需要显示的数据
)
fig.update_traces(textposition="outside", showlegend=False, text=[["a"]*11, ["b"]*11, ["c"]*11, ["d"]*11,["e"]*11])
fig.show()

In [33]:
df = px.data.gapminder()
df

country continent  year  lifeExp       pop   gdpPercap iso_alpha  \
0     Afghanistan      Asia  1952   28.801   8425333  779.445314       AFG   
1     Afghanistan      Asia  1957   30.332   9240934  820.853030       AFG   
2     Afghanistan      Asia  1962   31.997  10267083  853.100710       AFG   
3     Afghanistan      Asia  1967   34.020  11537966  836.197138       AFG   
4     Afghanistan      Asia  1972   36.088  13079460  739.981106       AFG   
...           ...       ...   ...      ...       ...         ...       ...   
1699     Zimbabwe    Africa  1987   62.351   9216418  706.157306       ZWE   
1700     Zimbabwe    Africa  1992   60.377  10704340  693.420786       ZWE   
1701     Zimbabwe    Africa  1997   46.809  11404948  792.449960       ZWE   
1702     Zimbabwe    Africa  2002   39.989  11926563  672.038623       ZWE   
1703     Zimbabwe    Africa  2007   43.487  12311143  469.709298       ZWE   

      iso_num  
0           4  
1           4  
2           4  
3           4  
4           4  
...       ...  
1699      716  
1700      716  
1701      716  
1702      716  
1703      716  

[1704 rows x 8 columns]